In [1]:
import warnings
warnings.filterwarnings(action='ignore')
%config Completer.use_jedi = False 
import requests
import folium
import pandas as pd
import numpy as np
from pandas.io.json import json_normalize
import json

In [2]:
# 따릉이 서버에 post 방식으로 요청을 해서 서버가 응답하는 
# 데이터를 받는다.
targetSite = 'https://www.bikeseoul.com/app/station/getStationRealtimeStatus.do'
request = requests.post(targetSite, data={
    'stationGrpSeq':'ALL'
})
# print(request) # <Response [200]>
# print(type(request.text)) # <class 'str'>
# print(request.text)

In [3]:
# 따릉이 서버가 응답은 json 형태의 문자열을 파이썬에서 
# 사용하기 위해서 딕셔너리 타입으로 변환한다.
# bike_json = json.loads(request.text) # json 모듈의 loads() 메소드 사용
bike_json = request.json() # 
# print(type(bike_json))  # <class 'dict'>
# print(bike_json.keys()) # dict_keys(['stationImgPath', 'appUserSessionVO', 'loginYn', 'realtimeList', 'sessionId', 'stationVO', 'checkResult'])
# print(bike_json)

In [4]:
# bike_json['realtimeList']
bike_json.get('realtimeList')

[{'stationId': 'ST-4',
  'stationImgFileName': '',
  'stationName': '102. 망원역 1번출구 앞',
  'stationLongitude': '126.91062927',
  'stationLatitude': '37.55564880',
  'rackTotCnt': '15',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '4',
  'parkingELECBikeCnt': '1',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationId': 'ST-5',
  'stationImgFileName': '',
  'stationName': '103. 망원역 2번출구 앞',
  'stationLongitude': '126.91083527',
  'stationLatitude': '37.55495071',
  'rackTotCnt': '14',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '5',
  'parkingELECBikeCnt': '3',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationId': 'ST-6',
  'stationImgFileName': '',
  'stationName': '104. 합정역 1번출구 앞',
  'stationLongitude': '126.91498566',
  'stationLatitude': '37.55062866',
  'rackTotCnt': '13',
  'parkingBikeTotCnt': '0',
  'parkingQRBikeCnt': '1',
  'parkingELECBikeCnt': '1',
  'stationSeCd': 'RAK_002',
  'mode': None},
 {'stationId': 'ST-7',
  'stationImgFileName': '',
  'stationNam

In [5]:
# pandas.io.json 모듈의 json_normalize() 메소드로 json 타입의 
# 데이터가 변환된 딕셔너리를 판다스 데이터프레임으로 변환한다.
# json_normalize(딕셔너리, '데이터프레임으로 변환할 데이터가 할당된 딕셔너리의 'key')
bike_df = json_normalize(bike_json, 'realtimeList')
bike_df 

stationId stationImgFileName             stationName stationLongitude  \
0         ST-4                            102. 망원역 1번출구 앞     126.91062927   
1         ST-5                            103. 망원역 2번출구 앞     126.91083527   
2         ST-6                            104. 합정역 1번출구 앞     126.91498566   
3         ST-7                            105. 합정역 5번출구 앞     126.91482544   
4         ST-8                            106. 합정역 7번출구 앞     126.91282654   
...        ...                ...                     ...              ...   
2714   ST-3239                             5870. LG트윈타워 앞     126.93008423   
2715   ST-3250                               5871. 건영상가 앞     126.90161133   
2716   ST-3161                              6053. 중부세무서 앞     126.99066162   
2717   ST-3210                     6054.청구e편한세상아파트 113동 앞     127.01821136   
2718   ST-3255                                 6055. 한국경제     126.96768188   

     stationLatitude rackTotCnt parkingBikeTotCnt parkingQRBikeCnt  \
0        37.55564880         15                 0                4   
1        37.55495071         14                 0                5   
2        37.55062866         13                 0                1   
3        37.55000687          5                 0                0   
4        37.54864502         12                 0                4   
...              ...        ...               ...              ...   
2714     37.52834702         10                 0                4   
2715     37.50611877         13                 0                7   
2716     37.56092453          5                 0                0   
2717     37.56104279          5                 0                9   
2718     37.56062698          8                 0                0   

     parkingELECBikeCnt stationSeCd  mode  
0                     1     RAK_002  None  
1                     3     RAK_002  None  
2                     1     RAK_002  None  
3                     0     RAK_002  None  
4                     0     RAK_002  None  
...                 ...         ...   ...  
2714                  0     RAK_002  None  
2715                  3     RAK_002  None  
2716                  0     RAK_002  None  
2717                  7     RAK_002  None  
2718                  1     RAK_002  None  

[2719 rows x 11 columns]

In [6]:
bike_df.columns

Index(['stationId', 'stationImgFileName', 'stationName', 'stationLongitude',
       'stationLatitude', 'rackTotCnt', 'parkingBikeTotCnt',
       'parkingQRBikeCnt', 'parkingELECBikeCnt', 'stationSeCd', 'mode'],
      dtype='object')

In [7]:
# 'stationId': 대여소 Id
# 'stationName': 대여소 이름
# 'stationLatitude': 대여소 위도
# 'stationLongitude': 대여소 경도 
# 'rackTotCnt': 주차 가능한 자전거 대수
# 'parkingBikeTotCnt': 주차된 따릉이 LCD형 대수 => 사용하지 않음
# 'parkingQRBikeCnt': 주차된 따릉이 QR 대수 => 일반 따릉이
# 'parkingELECBikeCnt': 새싹 따릉이

bike_df_map = bike_df[
    [
        'stationId', # 대여소 Id
        'stationName', # 대여소 이름
        'stationLatitude', # 대여소 위도
        'stationLongitude', # 대여소 경도 
        'parkingQRBikeCnt', # 일반 따릉이
        'parkingELECBikeCnt' # 새싹 따릉이
    ]
]
del bike_df
bike_df_map

stationId             stationName stationLatitude stationLongitude  \
0         ST-4         102. 망원역 1번출구 앞     37.55564880     126.91062927   
1         ST-5         103. 망원역 2번출구 앞     37.55495071     126.91083527   
2         ST-6         104. 합정역 1번출구 앞     37.55062866     126.91498566   
3         ST-7         105. 합정역 5번출구 앞     37.55000687     126.91482544   
4         ST-8         106. 합정역 7번출구 앞     37.54864502     126.91282654   
...        ...                     ...             ...              ...   
2714   ST-3239          5870. LG트윈타워 앞     37.52834702     126.93008423   
2715   ST-3250            5871. 건영상가 앞     37.50611877     126.90161133   
2716   ST-3161           6053. 중부세무서 앞     37.56092453     126.99066162   
2717   ST-3210  6054.청구e편한세상아파트 113동 앞     37.56104279     127.01821136   
2718   ST-3255              6055. 한국경제     37.56062698     126.96768188   

     parkingQRBikeCnt parkingELECBikeCnt  
0                   4                  1  
1                   5                  3  
2                   1                  1  
3                   0                  0  
4                   4                  0  
...               ...                ...  
2714                4                  0  
2715                7                  3  
2716                0                  0  
2717                9                  7  
2718                0                  1  

[2719 rows x 6 columns]

In [8]:
# bike_df_map.dtypes
bike_df_map.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2719 entries, 0 to 2718
Data columns (total 6 columns):
 #   Column              Non-Null Count  Dtype 
---  ------              --------------  ----- 
 0   stationId           2719 non-null   object
 1   stationName         2719 non-null   object
 2   stationLatitude     2719 non-null   object
 3   stationLongitude    2719 non-null   object
 4   parkingQRBikeCnt    2719 non-null   object
 5   parkingELECBikeCnt  2719 non-null   object
dtypes: object(6)
memory usage: 127.6+ KB


In [9]:
# astype() 메소드로 위도, 경도 데이터 타입을 object에서 float로 
# 변환한다.
bike_df_map['stationLatitude'] = bike_df_map['stationLatitude'].astype(float)
bike_df_map['stationLongitude'] = bike_df_map['stationLongitude'].astype(float)
bike_df_map['parkingQRBikeCnt'] = bike_df_map['parkingQRBikeCnt'].astype(float)
bike_df_map['parkingELECBikeCnt'] = bike_df_map['parkingELECBikeCnt'].astype(float)
bike_df_map['parkingTotBikeCnt'] = bike_df_map['parkingQRBikeCnt'] + bike_df_map['parkingELECBikeCnt']
bike_df_map

stationId             stationName  stationLatitude  stationLongitude  \
0         ST-4         102. 망원역 1번출구 앞        37.555649        126.910629   
1         ST-5         103. 망원역 2번출구 앞        37.554951        126.910835   
2         ST-6         104. 합정역 1번출구 앞        37.550629        126.914986   
3         ST-7         105. 합정역 5번출구 앞        37.550007        126.914825   
4         ST-8         106. 합정역 7번출구 앞        37.548645        126.912827   
...        ...                     ...              ...               ...   
2714   ST-3239          5870. LG트윈타워 앞        37.528347        126.930084   
2715   ST-3250            5871. 건영상가 앞        37.506119        126.901611   
2716   ST-3161           6053. 중부세무서 앞        37.560925        126.990662   
2717   ST-3210  6054.청구e편한세상아파트 113동 앞        37.561043        127.018211   
2718   ST-3255              6055. 한국경제        37.560627        126.967682   

      parkingQRBikeCnt  parkingELECBikeCnt  parkingTotBikeCnt  
0                  4.0                 1.0                5.0  
1                  5.0                 3.0                8.0  
2                  1.0                 1.0                2.0  
3                  0.0                 0.0                0.0  
4                  4.0                 0.0                4.0  
...                ...                 ...                ...  
2714               4.0                 0.0                4.0  
2715               7.0                 3.0               10.0  
2716               0.0                 0.0                0.0  
2717               9.0                 7.0               16.0  
2718               0.0                 1.0                1.0  

[2719 rows x 7 columns]

In [10]:
bike_df_map.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2719 entries, 0 to 2718
Data columns (total 7 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   stationId           2719 non-null   object 
 1   stationName         2719 non-null   object 
 2   stationLatitude     2719 non-null   float64
 3   stationLongitude    2719 non-null   float64
 4   parkingQRBikeCnt    2719 non-null   float64
 5   parkingELECBikeCnt  2719 non-null   float64
 6   parkingTotBikeCnt   2719 non-null   float64
dtypes: float64(5), object(2)
memory usage: 148.8+ KB


In [11]:
# bike_df_map.to_csv('./data/bike_df_map.csv', index=False)

Geo coding  

지오코딩 => 주소로 위도, 경도 얻기, 역지오코딩=> 위도, 경도로 주소 얻기  
pip install geopy

In [12]:
from geopy.geocoders import Nominatim

In [13]:
# 주소를 인수로 넘겨받아 위도, 경도를 리턴하는 함수
def geocoding(address):
    geolocoder = Nominatim(user_agent='South Korea', timeout=None)
    geo = geolocoder.geocode(address)
    return {'위도': geo.latitude, '경도': geo.longitude}
    
# address = geocoding('서울시 서대문구 홍제1동')
# print(address)

In [14]:
# 위도, 경도를 넘겨받아 주소를 리턴하는 함수
def geocoding_reverse(lat_lot):
    geolocoder = Nominatim(user_agent='South Korea', timeout=None)
    return geolocoder.geocode(lat_lot)

address = geocoding_reverse('37.5697599,126.9836604')
# print(type(address)) # <class 'geopy.location.Location'>
# print(address)
addr = str(address).split(', ')
# print(type(addr)) # 
# print(addr) # ['54', '종로8길', '공평동', '종로1·2·3·4가동', '종로구', '서울', '04540', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geocoding_reverse('35.1852527,129.1240061')
addr = str(address).split(', ')
# print(addr) # ['해운대로143번길', '재송동', '재송1동', '해운대구', '부산', '48056', '대한민국']
print(addr[-3], addr[-4], addr[-5])

address = geocoding_reverse('36.7590374,128.0729759')
addr = str(address).split(', ')
# print(addr) # ['하초리', '문경시', '경상북도', '36919', '대한민국']
print(addr[-3], addr[-4], addr[-5])

pass

서울 성북구 성북동
부산 해운대구 재송1동
경상북도 문경시 하초리


In [15]:
bike_df_map['gu'] = np.NaN
bike_df_map['dong'] = np.NaN
bike_df_map

stationId             stationName  stationLatitude  stationLongitude  \
0         ST-4         102. 망원역 1번출구 앞        37.555649        126.910629   
1         ST-5         103. 망원역 2번출구 앞        37.554951        126.910835   
2         ST-6         104. 합정역 1번출구 앞        37.550629        126.914986   
3         ST-7         105. 합정역 5번출구 앞        37.550007        126.914825   
4         ST-8         106. 합정역 7번출구 앞        37.548645        126.912827   
...        ...                     ...              ...               ...   
2714   ST-3239          5870. LG트윈타워 앞        37.528347        126.930084   
2715   ST-3250            5871. 건영상가 앞        37.506119        126.901611   
2716   ST-3161           6053. 중부세무서 앞        37.560925        126.990662   
2717   ST-3210  6054.청구e편한세상아파트 113동 앞        37.561043        127.018211   
2718   ST-3255              6055. 한국경제        37.560627        126.967682   

      parkingQRBikeCnt  parkingELECBikeCnt  parkingTotBikeCnt  gu  dong  
0                  4.0                 1.0                5.0 NaN   NaN  
1                  5.0                 3.0                8.0 NaN   NaN  
2                  1.0                 1.0                2.0 NaN   NaN  
3                  0.0                 0.0                0.0 NaN   NaN  
4                  4.0                 0.0                4.0 NaN   NaN  
...                ...                 ...                ...  ..   ...  
2714               4.0                 0.0                4.0 NaN   NaN  
2715               7.0                 3.0               10.0 NaN   NaN  
2716               0.0                 0.0                0.0 NaN   NaN  
2717               9.0                 7.0               16.0 NaN   NaN  
2718               0.0                 1.0                1.0 NaN   NaN  

[2719 rows x 9 columns]

In [16]:
'''
for i in range(bike_df_map.shape[0])[:]:
    lat_lot = '{},{}'.format(bike_df_map.loc[i,'stationLatitude'], bike_df_map.loc[i,'stationLongitude'])
    addr = str(geocoding_reverse(lat_lot)).split(', ')
    # print(addr[-4], addr[-5])
    try:
        bike_df_map.loc[i,'gu'] = addr[-4]
    except:
        print('{}번째 인덱스 스테이션의 -4번째 주소 없음'.format(i))
    try:
        bike_df_map.loc[i,'dong'] = addr[-5]
    except:
        print('{}번째 인덱스 스테이션의 -5번째 주소 없음'.format(i))

bike_df_map
'''
pass

In [17]:
# bike_df_map.to_csv('./data/bike_20230907.csv', index=False)

In [50]:
bike_df_map = pd.read_csv('./data/bike_20230907.csv', encoding='cp949')
bike_df_map

stationId             stationName  stationLongitude  stationLatitude  \
0         ST-4         102. 망원역 1번출구 앞        126.910629        37.555649   
1         ST-5         103. 망원역 2번출구 앞        126.910835        37.554951   
2         ST-6         104. 합정역 1번출구 앞        126.914986        37.550629   
3         ST-7         105. 합정역 5번출구 앞        126.914825        37.550007   
4         ST-8         106. 합정역 7번출구 앞        126.912826        37.548645   
...        ...                     ...               ...              ...   
2713   ST-3239          5870. LG트윈타워 앞        126.930084        37.528347   
2714   ST-3250            5871. 건영상가 앞        126.901611        37.506119   
2715   ST-3161           6053. 중부세무서 앞        126.990662        37.560925   
2716   ST-3210  6054.청구e편한세상아파트 113동 앞        127.018211        37.561043   
2717   ST-3255              6055. 한국경제        126.967682        37.560627   

      parkingQRBikeCnt  parkingELECBikeCnt  parkingTotBikeCnt    gu  dong  
0                    5                   1                  6   마포구   서교동  
1                    2                   3                  5   마포구  망원1동  
2                    5                   1                  6   마포구   서교동  
3                    2                   0                  2   마포구   서교동  
4                    4                   0                  4   마포구   합정동  
...                ...                 ...                ...   ...   ...  
2713                 8                   0                  8  영등포구   여의동  
2714                 9                   3                 12  영등포구  신길3동  
2715                 0                   0                  0    중구    필동  
2716                 4                   7                 11    중구   동화동  
2717                 1                   0                  1   중랑구  망우본동  

[2718 rows x 9 columns]

In [41]:
bike_df_map[bike_df_map.gu.isnull() | bike_df_map.dong.isnull()]

stationId          stationName  stationLongitude  stationLatitude  \
46      ST-212      155. 가좌역1 번출구 앞        126.915047        37.568295   
66      ST-232      179. 가좌역 4번출구 앞        126.915299        37.568775   
1368   ST-2352      2079.중앙대학교 중앙광장        126.957779        37.506672   
2123   ST-3225  3934. 철도교통관제센터 정문 앞        126.877884        37.497082   
2553   ST-3024   4837. 양원지구 힐데스하임 앞        127.106209        37.609241   

      parkingQRBikeCnt  parkingELECBikeCnt  parkingTotBikeCnt     gu dong  
46                   4                   4                  8   성산2동  NaN  
66                  27                   0                 27  남가좌1동  NaN  
1368                 4                   1                  5    흑석동  NaN  
2123                13                  11                 24   구로1동  NaN  
2553                 8                   0                  8   망우본동  NaN

In [42]:
bike_df_map[bike_df_map.gu.isnull() | bike_df_map.dong.isnull()].stationId

46       ST-212
66       ST-232
1368    ST-2352
2123    ST-3225
2553    ST-3024
Name: stationId, dtype: object

In [43]:
errorList = list(bike_df_map[bike_df_map.gu.isnull() | bike_df_map.dong.isnull()].stationId)
# print(type(errorList)) # <class 'list'>
print(errorList)

['ST-212', 'ST-232', 'ST-2352', 'ST-3225', 'ST-3024']


In [49]:
for error in errorList:
    bike_error = bike_df_map[bike_df_map.stationId == error]
    lat_lot = '{},{}'.format(bike_error.iloc[0,2], bike_error.iloc[0, 3])
    address = geocoding_reverse(lat_lot)
    addr = str(address).split(', ')
    bike_df_map.loc[bike_error.index,'gu'] = addr[-3]
    bike_df_map.loc[bike_error.index,'dong'] = addr[-4]
    
bike_df_map[bike_df_map.gu.isnull() | bike_df_map.dong.isnull()]

Empty DataFrame
Columns: [stationId, stationName, stationLongitude, stationLatitude, parkingQRBikeCnt, parkingELECBikeCnt, parkingTotBikeCnt, gu, dong]
Index: []

In [27]:
# bike_df_map.to_csv('./data/bike_20230907.csv', index=False)

In [52]:
bike_map = folium.Map(location=[bike_df_map.stationLatitude.mean(),
                                bike_df_map.stationLongitude.mean()], zoom_start=12)

for index, data in bike_df_map.iterrows():
    
    station = data.stationName.split('.')
    '''
    if len(station) == 1:
        stationName = station[0].strip()
    else:
        stationName = station[1].strip()
    '''    
    stationName = station[0].strip() if len(station) == 1 else station[1].strip()
    
    string = '{}. 일반: {:.0f}대, 새싹: {:.0f}대'.format(
    stationName, data.parkingQRBikeCnt, data.parkingELECBikeCnt)
    # print(string)
    stationInfo = folium.Popup(string, max_width=300)
    folium.Marker([data.stationLatitude, data.stationLongitude], 
        popup=stationInfo, icon=folium.Icon(color='green', 
        icon='hand-down')).add_to(bike_map)
    
bike_map.save('./output/bike.html')  
bike_map # 지도 생성

종로구 따릉이 스테이션 위치

In [35]:
bike_df_map_gu = bike_df_map[bike_df_map.gu == '종로구']
bike_df_map_gu

stationId            stationName  stationLongitude  stationLatitude  \
168     ST-117       301. 경복궁역 7번출구 앞        126.971451        37.575794   
169     ST-118       302. 경복궁역 4번출구 뒤        126.974060        37.575947   
170     ST-119       303. 광화문역 1번출구 앞        126.974663        37.571770   
171     ST-121            305. 종로구청 옆        126.978332        37.572559   
172     ST-123         307. 서울역사박물관 앞        126.971100        37.570000   
...        ...                    ...               ...              ...   
2497   ST-2473           4710. 자교교회 앞        126.971237        37.581146   
2498   ST-2427  4711. 올림픽기념 국민생활관 로터리        126.999344        37.589836   
2500   ST-2923       4715. 돈의문 박물관 마을        126.969551        37.568836   
2501   ST-3075    4718. 광화문역 6번출구 옆 A        126.976433        37.569931   
2502   ST-3090        4719. 종로문화원 건너편        126.980507        37.575714   

      parkingQRBikeCnt  parkingELECBikeCnt  parkingTotBikeCnt   gu  \
168                  1                   0                  1  종로구   
169                  3                   0                  3  종로구   
170                 21                   3                 24  종로구   
171                  3                   1                  4  종로구   
172                  1                   0                  1  종로구   
...                ...                 ...                ...  ...   
2497                 2                   0                  2  종로구   
2498                 4                   2                  6  종로구   
2500                 0                   0                  0  종로구   
2501                 0                   0                  0  종로구   
2502                 4                   0                  4  종로구   

             dong  
168           사직동  
169           사직동  
170           사직동  
171   종로1·2·3·4가동  
172           사직동  
...           ...  
2497        청운효자동  
2498          혜화동  
2500          사직동  
2501          사직동  
2502  종로1·2·3·4가동  

[84 rows x 9 columns]

In [36]:
bike_map = folium.Map(location=[bike_df_map_gu.stationLatitude.mean(),bike_df_map_gu.stationLongitude.mean()], zoom_start=14)
# iterrows() 메소드는 데이터프레임에 저장된 데이터의 인덱스와 
# 데이터를 리턴한다.
for index, data in bike_df_map_gu.iterrows():
    
    station = data.stationName.split('.')
    '''
    if len(station) == 1:
        stationName = station[0].strip()
    else:
        stationName = station[1].strip()
    '''    
    stationName = station[0].strip() if len(station) == 1 else station[1].strip()
    
    string = '{}. 일반: {:.0f}대, 새싹: {:.0f}대'.format(stationName, data.parkingQRBikeCnt, data.parkingELECBikeCnt)
#     print(string)
    stationInfo = folium.Popup(string, max_width=300)
    folium.Marker([data.stationLatitude, data.stationLongitude], popup=stationInfo,
                 icon=folium.Icon(color='green', icon='hand-down')).add_to(bike_map)
    
bike_map.save('./output/bike_gu.html')  
bike_map # 지도 생성